In [1]:
import numpy as np

import scipy as sp
from scipy import spatial

import matplotlib.pyplot as plt # side-stepping mpl backend

from nltk.stem.lancaster import LancasterStemmer

from sklearn.metrics.pairwise import cosine_similarity
from sklearn.feature_extraction.text import TfidfVectorizer, CountVectorizer
from sklearn.metrics import pairwise
from sklearn.feature_selection import SelectPercentile, f_classif
from sklearn import cross_validation
import heapq
import string
import re

from nltk.corpus import stopwords
from collections import defaultdict

vectorizer = CountVectorizer()
st = LancasterStemmer()

/usr/local/lib/python3.5/dist-packages/sklearn/cross_validation.py:44: DeprecationWarning: This module was deprecated in version 0.18 in favor of the model_selection module into which all the refactored classes and functions are moved. Also note that the interface of the new CV iterators are different from that of this module. This module will be removed in 0.20.
  "This module will be removed in 0.20.", DeprecationWarning)


In [2]:
with open("TestData/train.dat", "r") as fh:
    #with open("TestData/Test/training_out.dat", "r") as fh:
    linesOfTrainData = fh.readlines()
print(len(linesOfTrainData))

#with open("TestData/format.dat", "r") as fh:
with open("TestData/Test/format_out.dat", "r") as fh:
    linesOfFormat = fh.readlines()
print(len(linesOfFormat))

with open("TestData/test.dat", "r") as fh:
#with open("TestData/Test/test_out.dat", "r") as fh:
    linesOfTestData = fh.readlines()
print(len(linesOfTestData))


18506
0
18506


In [3]:
##stopwords and stemming for Training

print ("First line before cleanup from Training Data: ",linesOfTrainData[0])

stops = set(stopwords.words('english'))

linesOfTrainDataAfterPreProcessing=[]
for line in linesOfTrainData:
    newLine = line
    for w in newLine.split():
        if w.lower() in stops:
            newLine = newLine.replace(' '+w+' ', ' ') # for identifting words
    linesOfTrainDataAfterPreProcessing.append(newLine)


linesOfTrainDataAfterSteming = []
for line in linesOfTrainDataAfterPreProcessing:
    newLine = line
    for w in newLine.split():
            newLine = newLine.replace(w, st.stem(w)) # for stemming
    linesOfTrainDataAfterSteming.append(newLine)
    
#Not working    
linesOfTrainDataAfterStemingWithoutPunctuation = []
for line in linesOfTrainDataAfterSteming:
    newLine = line
    for w in newLine.split():
         if w in string.punctuation:
            newLine = newLine.replace(w,re.sub(r'[^\w\s]()','',w)) # for Punctuation 
    linesOfTrainDataAfterStemingWithoutPunctuation.append(newLine)    


linesOfTrainData = linesOfTrainDataAfterStemingWithoutPunctuation

print ("\n\nFirst line after cleanup from Training Data: ",linesOfTrainData[0])

First line before cleanup from Training Data:  +1	This book is such a life saver.  It has been so helpful to be able to go back to track trends, answer pediatrician questions, or communicate with each other when you are up at different times of the night with a newborn.  I think it is one of those things that everyone should be required to have before they leave the hospital.  We went through all the pages of the newborn version, then moved to the infant version, and will finish up the second infant book (third total) right as our baby turns 1.  See other things that are must haves for baby at [...]



First line after cleanup from Training Data:  +1	thi book lif saver.  help abl go back track trends, answ pedy questions, commun diff tim night newborn.  think on thing everyon requir leav hospital.  went pag newborn version, mov inf version, fin second inf book (third total) right baby turn 1.  see thing must hav baby [...]



In [4]:
##stopwords and stemming for Testdata

print ("First line before cleanup from Test Data: ",linesOfTestData[0])

stops = set(stopwords.words('english'))

linesOfTestDataAfterPreProcessing=[]
for line in linesOfTestData:
    newLine = line
    for w in newLine.split():
        if w.lower() in stops:
            newLine = newLine.replace(' '+w+' ', ' ') # for identifting words
    linesOfTestDataAfterPreProcessing.append(newLine)


linesOfTestDataAfterSteming = []
for line in linesOfTestDataAfterPreProcessing:
    newLine = line
    for w in newLine.split():
            newLine = newLine.replace(w, st.stem(w)) # for stemming
    linesOfTestDataAfterSteming.append(newLine)
    
    
    

linesOfTestData = linesOfTestDataAfterSteming

print ("\n\nFirst line after cleanup from Test Data: ",linesOfTestData[0])

First line before cleanup from Test Data:  Perfect for new parents. We were able to keep track of baby's feeding, sleep and diaper change schedule for the first two and a half months of her life. Made life easier when the doctor would ask questions about habits because we had it all right there!



First line after cleanup from Test Data:  perfect new parents. abl keep track baby's feeding, sleep diap chang schedule first two half month lif. mad lif easy doct would ask quest habit right there!



In [5]:
# get a frequency count for all words in the Training docs
wordsInSet = {}
for d in linesOfTrainData:
    for w in d.split():
        if w == "+1" or w == "-1":
            continue
        else:
            if w not in wordsInSet:
                wordsInSet[w] = 1
            else:
                wordsInSet[w] += 1
print("Number of unique words: %d." % len(wordsInSet))


Number of unique words: 63829.


In [6]:
# get a frequency count for all words in the Test docs

for d in linesOfTestData:
    for w in d.split():
        if w not in wordsInSet:
            wordsInSet[w] = 1
        else:
            wordsInSet[w] += 1
print("Number of unique words: %d." % len(wordsInSet))
print(wordsInSet["great"])

Number of unique words: 101729.
4


In [10]:
from collections import Counter
c = Counter(wordsInSet)

top_percentile = 0.2 # 0.2 Precentile
features = c.most_common(int(round(len(c)*top_percentile)))
features_counts = len(features)
print(features_counts)

featureList = []
for key in features:
       featureList.append(key)

print (featureList)
#top_percentile = 0.5
# features_counts = len(words.most_common(int(round(len(words)*top_percentile))))

20346
[('us', 27110), ('baby', 18861), ('on', 16443), ('get', 16217), ('lik', 14352), ('would', 14077), ("it's", 12680), ('i', 11563), ('lov', 11059), ('real', 10458), ('easy', 10252), ('work', 9236), ('littl', 8583), ('ev', 8359), ('gre', 8337), ('it.', 8299), ('put', 8275), ("don't", 8165), ('tim', 7517), ('much', 7356), ('also', 7198), ('mak', 7165), ('bottl', 7041), ('old', 6883), ('bought', 6747), ('son', 6681), ('fit', 6376), ('look', 6315), ('keep', 6003), ('seat', 5975), ('stil', 5886), ('nee', 5690), ('first', 5589), ('good', 5577), ('got', 5572), ('tak', 5544), ('back', 5434), ('buy', 5370), ('produc', 5363), ('want', 5346), ("doesn't", 5272), ('thing', 5102), ('could', 5010), ('daught', 4952), ("didn't", 4893), ('diap', 4836), ('thi', 4770), ('wel', 4706), ('seem', 4632), ("i'm", 4602), ('hold', 4515), ('think', 4491), ('month', 4489), ('com', 4424), ('recommend', 4407), ('two', 4362), ('sint', 4350), ('wash', 4270), ('around', 4102), ('way', 4099), ('smal', 4079), ('2', 402

In [155]:
#Buid matrix

from collections import Counter
from scipy.sparse import csr_matrix
def build_matrix(docs):
    r""" Build sparse matrix from a list of documents, 
    each of which is a list of word/terms in the document.  
    """
    nrows = len(docs)
    idx = features
    tid = 0
    nnz = 0
    for d in docs:
        nnz += len(set(d))
        print("d: ",d)
        for w in d:
            if w not in idx:
                idx[w] = tid
                tid += 1
    ncols = len(idx)
    print(idx)
        
    # set up memory
    ind = np.zeros(nnz, dtype=np.int)
    val = np.zeros(nnz, dtype=np.double)
    ptr = np.zeros(nrows+1, dtype=np.int)
    i = 0  # document ID / row counter
    n = 0  # non-zero counter
    # transfer values
    for d in docs:
        cnt = Counter(d)
        keys = list(k for k,_ in cnt.most_common())
        l = len(keys)
        for j,k in enumerate(keys):
            ind[j+n] = idx[k]
            val[j+n] = cnt[k]
        ptr[i+1] = ptr[i] + l
        n += l
        i += 1
            
    mat = csr_matrix((val, ind, ptr), shape=(nrows, ncols), dtype=np.double)
    mat.sort_indices()
    
    return mat


def csr_info(mat, name="", non_empy=False):
    r""" Print out info about this CSR matrix. If non_empy, 
    report number of non-empty rows and cols as well
    """
    if non_empy:
        print("%s [nrows %d (%d non-empty), ncols %d (%d non-empty), nnz %d]" % (
                name, mat.shape[0], 
                sum(1 if mat.indptr[i+1] > mat.indptr[i] else 0 
                for i in range(mat.shape[0])), 
                mat.shape[1], len(np.unique(mat.indices)), 
                len(mat.data)))
    else:
        print( "%s [nrows %d, ncols %d, nnz %d]" % (name, 
                mat.shape[0], mat.shape[1], len(mat.data)) )

In [156]:
# #Buid matrix

# from collections import Counter
# from scipy.sparse import csr_matrix
# def build_matrix(docs):
#     r""" Build sparse matrix from a list of documents, 
#     each of which is a list of word/terms in the document.  
#     """
#     nrows = len(docs)
#     idx = {}
#     tid = 0
#     nnz = 0
#     for d in docs:
#         nnz += len(set(d))
#         for w in d:
#             if w not in idx:
#                 idx[w] = tid
#                 tid += 1
#     ncols = len(idx)
#     print(idx)
        
#     # set up memory
#     ind = np.zeros(nnz, dtype=np.int)
#     val = np.zeros(nnz, dtype=np.double)
#     ptr = np.zeros(nrows+1, dtype=np.int)
#     i = 0  # document ID / row counter
#     n = 0  # non-zero counter
#     # transfer values
#     for d in docs:
#         cnt = Counter(d)
#         keys = list(k for k,_ in cnt.most_common())
#         l = len(keys)
#         for j,k in enumerate(keys):
#             ind[j+n] = idx[k]
#             val[j+n] = cnt[k]
#         ptr[i+1] = ptr[i] + l
#         n += l
#         i += 1
            
#     mat = csr_matrix((val, ind, ptr), shape=(nrows, ncols), dtype=np.double)
#     mat.sort_indices()
    
#     return mat


# def csr_info(mat, name="", non_empy=False):
#     r""" Print out info about this CSR matrix. If non_empy, 
#     report number of non-empty rows and cols as well
#     """
#     if non_empy:
#         print("%s [nrows %d (%d non-empty), ncols %d (%d non-empty), nnz %d]" % (
#                 name, mat.shape[0], 
#                 sum(1 if mat.indptr[i+1] > mat.indptr[i] else 0 
#                 for i in range(mat.shape[0])), 
#                 mat.shape[1], len(np.unique(mat.indices)), 
#                 len(mat.data)))
#     else:
#         print( "%s [nrows %d, ncols %d, nnz %d]" % (name, 
#                 mat.shape[0], mat.shape[1], len(mat.data)) )

In [ ]:
#print(linesOfTrainData[:1])
docslinesOfTrainData = [l.split() for l in linesOfTrainData]
matOflinesOfTrainData  = build_matrix(docslinesOfTrainData)
csr_info(matOflinesOfTrainData)

#print (matOflinesOfTrainData[:1])

#print(linesOfTestData[:1])
docslinesOfTestData = [l.split() for l in linesOfTestData]
matOflinesOfTestData  = build_matrix(docslinesOfTestData)
csr_info(matOflinesOfTestData)
#print (matOflinesOfTestData[:1])







d:  ['+1', 'thi', 'book', 'lif', 'saver.', 'help', 'abl', 'go', 'back', 'track', 'trends,', 'answ', 'pedy', 'questions,', 'commun', 'diff', 'tim', 'night', 'newborn.', 'think', 'on', 'thing', 'everyon', 'requir', 'leav', 'hospital.', 'went', 'pag', 'newborn', 'version,', 'mov', 'inf', 'version,', 'fin', 'second', 'inf', 'book', '(third', 'total)', 'right', 'baby', 'turn', '1.', 'see', 'thing', 'must', 'hav', 'baby', '[...]']
w:  +1
tid:  0
w:  thi
tid:  1
w:  book
tid:  2
w:  lif
tid:  3
w:  saver.
tid:  4
w:  help
tid:  5
w:  abl
tid:  6
w:  go
tid:  7
w:  back
tid:  8
w:  track
tid:  9
w:  trends,
tid:  10
w:  answ
tid:  11
w:  pedy
tid:  12
w:  questions,
tid:  13
w:  commun
tid:  14
w:  diff
tid:  15
w:  tim
tid:  16
w:  night
tid:  17
w:  newborn.
tid:  18
w:  think
tid:  19
w:  on
tid:  20
w:  thing
tid:  21
w:  everyon
tid:  22
w:  requir
tid:  23
w:  leav
tid:  24
w:  hospital.
tid:  25
w:  went
tid:  26
w:  pag
tid:  27
w:  newborn
tid:  28
w:  version,
tid:  29
w:  mov
tid:  

In [82]:
# scale matrix and normalize its rows
def csr_idf(mat, copy=False, **kargs):
    r""" Scale a CSR matrix by idf. 
    Returns scaling factors as dict. If copy is True, 
    returns scaled matrix and scaling factors.
    """
    if copy is True:
        mat = mat.copy()
    nrows = mat.shape[0]
    nnz = mat.nnz
    ind, val, ptr = mat.indices, mat.data, mat.indptr
    # document frequency
    df = defaultdict(int)
    for i in ind:
        df[i] += 1
    # inverse document frequency
    for k,v in df.items():
        df[k] = np.log(nrows / float(v))  ## df turns to idf - reusing memory
    # scale by idf
    for i in range(0, nnz):
        val[i] *= df[ind[i]]
        
    return df if copy is False else mat

def csr_l2normalize(mat, copy=False, **kargs):
    r""" Normalize the rows of a CSR matrix by their L-2 norm. 
    If copy is True, returns a copy of the normalized matrix.
    """
    if copy is True:
        mat = mat.copy()
    nrows = mat.shape[0]
    nnz = mat.nnz
    ind, val, ptr = mat.indices, mat.data, mat.indptr
    # normalize
    for i in range(nrows):
        rsum = 0.0    
        for j in range(ptr[i], ptr[i+1]):
            rsum += val[j]**2
        if rsum == 0.0:
            continue  # do not normalize empty rows
        rsum = 1.0/np.sqrt(rsum)
        for j in range(ptr[i], ptr[i+1]):
            val[j] *= rsum
            
    if copy is True:
        return mat

In [93]:
mat2linesOfTrainData = csr_idf(matOflinesOfTrainData, copy=True)
mat3linesOfTrainData = csr_l2normalize(mat2linesOfTrainData, copy=True)
print("mat1:", matOflinesOfTrainData[15,:20].todense(), "\n")
print("mat2:", mat2linesOfTrainData[15,:20].todense(), "\n")
print("mat3:", mat3linesOfTrainData[15,:20].todense())

mat1: [[ 1.  0.  0.  0.  0.  1.  0.  0.  0.  1.  0.  0.  0.  0.  0.  0.  0.  0.
   0.  0.]] 

mat2: [[ 0.61550991  0.          0.          0.          0.          2.72335093
   0.          0.          0.          5.59174378  0.          0.          0.
   0.          0.          0.          0.          0.          0.          0.        ]] 

mat3: [[ 0.01839653  0.          0.          0.          0.          0.08139626
   0.          0.          0.          0.16712757  0.          0.          0.
   0.          0.          0.          0.          0.          0.          0.        ]]


In [94]:

mat2linesOfTestData = csr_idf(matOflinesOfTestData, copy=True)
mat3linesOfTestData = csr_l2normalize(mat2linesOfTestData, copy=True)
print("mat1:", matOflinesOfTestData[15,:20].todense(), "\n")
print("mat2:", mat2linesOfTestData[15,:20].todense(), "\n")
print("mat3:", mat3linesOfTestData[15,:20].todense())



mat1: [[ 0.  0.  0.  1.  2.  0.  0.  1.  1.  0.  0.  1.  0.  0.  0.  0.  0.  1.
   0.  0.]] 

mat2: [[ 0.          0.          0.          2.66655838  4.03424195  0.          0.
   6.16228864  2.80834414  0.          0.          7.52326519  0.          0.
   0.          0.          0.          2.55762726  0.          0.        ]] 

mat3: [[ 0.          0.          0.          0.08845562  0.13382471  0.          0.
   0.20441671  0.09315897  0.          0.          0.2495633   0.          0.
   0.          0.          0.          0.08484214  0.          0.        ]]


In [95]:
linesOfTrainData_Transformed = mat3linesOfTrainData
linesOfTestData_Transformed = mat3linesOfTestData

In [96]:
# features_train, features_test, labels_train, labels_test = cross_validation.train_test_split(linesOfTrainData, linesOfTestData, test_size= 0.1,train_size= 0.9, random_state=42)


# vectorizer = TfidfVectorizer(sublinear_tf=True, max_df=0.5, stop_words='english')
# #linesOfTrainData_Transformed =  vectorizer.fit_transform(features_train)
# linesOfTrainData_Transformed =  vectorizer.fit_transform(linesOfTrainData)

# print (len(vectorizer.vocabulary_)) # after loading vocab from 1 source
# print(vectorizer.vocabulary_['younger'])
# linesOfTrainData_Transformed =  vectorizer.fit_transform(linesOfTestData)
# print (len(vectorizer.vocabulary_)) # after loading vocab from 2nd source
# print(vectorizer.vocabulary_['younger'])


# #linesOfTestData_Transformed = vectorizer.transform(features_test)
# linesOfTestData_Transformed = vectorizer.transform(linesOfTestData)

In [97]:
print(docslinesOfTrainData[:1]) 
print('-------')
print(linesOfTrainData_Transformed[:1])

[['+1', 'thi', 'book', 'lif', 'saver.', 'help', 'abl', 'go', 'back', 'track', 'trends,', 'answ', 'pedy', 'questions,', 'commun', 'diff', 'tim', 'night', 'newborn.', 'think', 'on', 'thing', 'everyon', 'requir', 'leav', 'hospital.', 'went', 'pag', 'newborn', 'version,', 'mov', 'inf', 'version,', 'fin', 'second', 'inf', 'book', '(third', 'total)', 'right', 'baby', 'turn', '1.', 'see', 'thing', 'must', 'hav', 'baby', '[...]']]
-------
  (0, 0)	0.0167483821515
  (0, 1)	0.0557516468449
  (0, 2)	0.286906915696
  (0, 3)	0.115849204935
  (0, 4)	0.187247198179
  (0, 5)	0.0741039604008
  (0, 6)	0.0718485390377
  (0, 7)	0.0685156302294
  (0, 8)	0.0591368801156
  (0, 9)	0.152154595795
  (0, 10)	0.248506155532
  (0, 11)	0.162029465048
  (0, 12)	0.172225091423
  (0, 13)	0.237473214453
  (0, 14)	0.185851477849
  (0, 15)	0.0732442593683
  (0, 16)	0.0482421079443
  (0, 17)	0.0866211691737
  (0, 18)	0.138973998171
  (0, 19)	0.0612729294095
  (0, 20)	0.0334597922937
  (0, 21)	0.118325466802
  (0, 22)	0.12

In [98]:

print(docslinesOfTestData[:1])
print('-------')
print(linesOfTestData_Transformed[:1])

[['perfect', 'new', 'parents.', 'abl', 'keep', 'track', "baby's", 'feeding,', 'sleep', 'diap', 'chang', 'schedule', 'first', 'two', 'half', 'month', 'lif.', 'mad', 'lif', 'easy', 'doct', 'would', 'ask', 'quest', 'habit', 'right', 'there!']]
-------
  (0, 0)	0.11740359889
  (0, 1)	0.121595409068
  (0, 2)	0.259086074095
  (0, 3)	0.115198278833
  (0, 4)	0.0871418629181
  (0, 5)	0.246893318528
  (0, 6)	0.136030218307
  (0, 7)	0.266217702365
  (0, 8)	0.121323580969
  (0, 9)	0.114896991304
  (0, 10)	0.119024505898
  (0, 11)	0.325013398624
  (0, 12)	0.089876220791
  (0, 13)	0.101495730537
  (0, 14)	0.165541847676
  (0, 15)	0.0986327427568
  (0, 16)	0.347081632017
  (0, 17)	0.110492333814
  (0, 18)	0.184260015333
  (0, 19)	0.0671917727854
  (0, 20)	0.259086074095
  (0, 21)	0.0569521716817
  (0, 22)	0.188079466727
  (0, 23)	0.257247451558
  (0, 24)	0.307496856341
  (0, 25)	0.116459465855
  (0, 26)	0.280532698074


In [99]:
# selector = SelectPercentile(f_classif, percentile=10)
# selector.fit(linesOfTrainData_Transformed, labels_train) #labels_train
# linesOfTrainData_Transformed = selector.transform(linesOfTrainData_Transformed)
# linesOfTestData_Transformed = selector.transform(linesOfTestData_Transformed)

In [100]:
# def CalculateCosine(vt,vs):
#         dotProduct = vt.dot(np.transpose(vS))#######
#         lengtht = np.linalg.norm(vt.data)
#         lengthS = np.linalg.norm(vS.data)

#         #handle exceptions

#         if lengthS!=0 and lengtht!=0 :
#             cosineSimilarityValue= dotProduct/(lengtht*lengthS)
#         else:
#             cosineSimilarityValue= 0
#         return cosineSimilarityValue

In [101]:

from sklearn.metrics.pairwise import cosine_similarity
def CalculateCosine(vt,vs):
        cosineSimilarityValue = cosine_similarity(vt,vs)
        return cosineSimilarityValue


In [102]:


# f = open('TestData/Test/format_out.dat', 'w')
# for vt in linesOfTestData_Transformed:
#     cosineSimilarityValues=[]
#     for vS in linesOfTrainData_Transformed:
#         cosineSimilarityValue = CalculateCosine(vt,vS)
#         cosineSimilarityValues.append(cosineSimilarityValue)

#     kneighbours = heapq.nlargest(3, cosineSimilarityValues)
#     #kneighbours = sp.sparse.csr_matrix.max(cosineSimilarityValues)

#     neighbourReviewTypeList = []
#     neighbourReviewTypeNegative = 0
#     neighbourReviewTypePositive = 0
#     print("@@@@@")
#     for neighbour in kneighbours:
#         index = cosineSimilarityValues.index(neighbour.data[0])
#         print("####",index)
#         if linesOfTrainData[index].strip()[0] == '-':
#             #neighbourReviewTypeList.append("-1")
#             neighbourReviewTypeNegative+=1
#         elif linesOfTrainData[index].strip()[0] == '+':
#             #neighbourReviewTypeList.append("+1")
#             neighbourReviewTypePositive+=1


#     if neighbourReviewTypeNegative > neighbourReviewTypePositive:
#         f.write('-1\n')
#     else:
#         f.write('+1\n')

# print("-----")


In [103]:
f = open('TestData/Test/format_out.dat', 'w')
for vt in linesOfTestData_Transformed:
    cosineSimilarityValues=[]
    for vS in linesOfTrainData_Transformed:
        cosineSimilarityValue = CalculateCosine(vt,vS)
        cosineSimilarityValues.append(cosineSimilarityValue)
    
    print(len(cosineSimilarityValues))
    kneighbours = heapq.nlargest(3, cosineSimilarityValues)
    #kneighbours = sp.sparse.csr_matrix.max(cosineSimilarityValues)
    print(kneighbours)
    neighbourReviewTypeList = []
    neighbourReviewTypeNegative = 0
    neighbourReviewTypePositive = 0
    print("@@@@@")
    for neighbour in kneighbours:
        index = cosineSimilarityValues.index(neighbour)
        print("####",index)
        if linesOfTrainData[index].strip()[0] == '-':
            #neighbourReviewTypeList.append("-1")
            neighbourReviewTypeNegative+=1
        elif linesOfTrainData[index].strip()[0] == '+':
            #neighbourReviewTypeList.append("+1")
            neighbourReviewTypePositive+=1


    if neighbourReviewTypeNegative > neighbourReviewTypePositive:
        f.write('-1\n')
    else:
        f.write('+1\n')

print("-----")

ValueError: Incompatible dimension for X and Y matrices: X.shape[1] == 63475 while Y.shape[1] == 63755